<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in Toronto (Old Version of the Link)</font></h1>

## Summary 

In this assignment, I will explore, segment, and cluster the neighborhoods in Toronto using the Foursquare API. 

The data for this work is not readily available on the internet and need to be scraped from the provided Wikipedia link ( https://en.wikipedia.org/w/index.php?title=List_of_postal_codes_of_Canada:_M&oldid=945633050). The link contains all the information we need to explore and cluster the neighborhoods in Toronto. 

In this notebook, we start by: 
1. **Data Wrangling**:

   In this step, we will scrape the Wikipedia page provided abobe to:
      1. wrangle the data, clean it, and then read it into a pandas dataframe so that it is in a structured format. The  dataframe will consist of three columns: PostalCode, Borough, and Neighborhood. The resulting data frame will be cleaned in such a way that **only the cells that have an assigned borough will be processed and cells a borough that is Not assigned will be ignored**. Also, more than one neighborhood can exist in one postal code area. For instance, in the table on the Wikipedia page, it can be noticed that M5A is listed twice and has two neighborhoods: Harbourfront and Regent Park. These two rows will be combined into one row with the neighborhoods separated with a comma. That is, If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough.

2. **Exploring Neighborhoods in Toronto, using k-Means Clustering**:

   In this step, we will use the **explore** function to get the most common venue categories in each neighborhood, and then  use this feature to group the neighborhoods into clusters. *k*-means clustering algorithm will be used to complete this task. 

3. Finally, we will use the Folium library to visualize the neighborhoods in Torronto and their emerging clusters.

In [57]:
#Downloading all the dependencies that will be needed 
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
#from sklearn.datasets.samples_generator import make_blobs

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

from bs4 import BeautifulSoup
import lxml

Libraries imported.


## Scraping the Wikipedia page for the table of postal codes of Canada

In [59]:
r = requests.get(' https://en.wikipedia.org/w/index.php?title=List_of_postal_codes_of_Canada:_M&oldid=945633050').text
soup=BeautifulSoup(r,'lxml')
print(soup.title)
from IPython.display import display_html
table = str(soup.table)
display_html(tab,raw=True)

<title>List of postal codes of Canada: M - Wikipedia</title>


Postcode 
 Borough 
 Neighbourhood
 
 
 M1A 
 Not assigned 
 Not assigned
 
 
 M2A 
 Not assigned 
 Not assigned
 
 
 M3A 
 North York 
 Parkwoods 
 
 
 M4A 
 North York 
 Victoria Village 
 
 
 M5A 
 Downtown Toronto 
 Harbourfront 
 
 
 M6A 
 North York 
 Lawrence Heights 
 
 
 M6A 
 North York 
 Lawrence Manor 
 
 
 M7A 
 Downtown Toronto 
 Queen's Park 
 
 
 M8A 
 Not assigned 
 Not assigned
 
 
 M9A 
 Etobicoke 
 Islington Avenue 
 
 
 M1B 
 Scarborough 
 Rouge 
 
 
 M1B 
 Scarborough 
 Malvern 
 
 
 M2B 
 Not assigned 
 Not assigned
 
 
 M3B 
 North York 
 Don Mills North
 
 
 M4B 
 East York 
 Woodbine Gardens 
 
 
 M4B 
 East York 
 Parkview Hill 
 
 
 M5B 
 Downtown Toronto 
 Ryerson
 
 
 M5B 
 Downtown Toronto 
 Garden District
 
 
 M6B 
 North York 
 Glencairn
 
 
 M7B 
 Not assigned 
 Not assigned
 
 
 M8B 
 Not assigned 
 Not assigned
 
 
 M9B 
 Etobicoke 
 Cloverdale
 
 
 M9B 
 Etobicoke 
 Islington 
 
 
 M9B 
 Etobicoke 
 Martin Grove
 
 
 M9B 
 Etobicoke 
 Princess Gardens 
 
 
 M9B 
 Etobicoke 
 West Deane Park 
 
 
 M1C 
 Scarborough 
 Highland Creek 
 
 
 M1C 
 Scarborough 
 Rouge Hill 
 
 
 M1C 
 Scarborough 
 Port Union 
 
 
 M2C 
 Not assigned 
 Not assigned
 
 
 M3C 
 North York 
 Flemingdon Park 
 
 
 M3C 
 North York 
 Don Mills South
 
 
 M4C 
 East York 
 Woodbine Heights 
 
 
 M5C 
 Downtown Toronto 
 St. James Town 
 
 
 M6C 
 York 
 Humewood-Cedarvale 
 
 
 M7C 
 Not assigned 
 Not assigned
 
 
 M8C 
 Not assigned 
 Not assigned
 
 
 M9C 
 Etobicoke 
 Bloordale Gardens
 
 
 M9C 
 Etobicoke 
 Eringate
 
 
 M9C 
 Etobicoke 
 Markland Wood 
 
 
 M9C 
 Etobicoke 
 Old Burnhamthorpe
 
 
 M1E 
 Scarborough 
 Guildwood
 
 
 M1E 
 Scarborough 
 Morningside 
 
 
 M1E 
 Scarborough 
 West Hill 
 
 
 M2E 
 Not assigned 
 Not assigned
 
 
 M3E 
 Not assigned 
 Not assigned
 
 
 M4E 
 East Toronto 
 The Beaches 
 
 
 M5E 
 Downtown Toronto 
 Berczy Park 
 
 
 M6E 
 York 
 Caledonia-Fairbanks
 
 
 M7E 
 Not assigned 
 Not assigned
 
 
 M8E 
 Not assigned 
 Not assigned
 
 
 M9E 
 Not assigned 
 Not assigned
 
 
 M1G 
 Scarborough 
 Woburn 
 
 
 M2G 
 Not assigned 
 Not assigned
 
 
 M3G 
 Not assigned 
 Not assigned
 
 
 M4G 
 East York 
 Leaside 
 
 
 M5G 
 Downtown Toronto 
 Central Bay Street
 
 
 M6G 
 Downtown Toronto 
 Christie
 
 
 M7G 
 Not assigned 
 Not assigned
 
 
 M8G 
 Not assigned 
 Not assigned
 
 
 M9G 
 Not assigned 
 Not assigned
 
 
 M1H 
 Scarborough 
 Cedarbrae
 
 
 M2H 
 North York 
 Hillcrest Village 
 
 
 M3H 
 North York 
 Bathurst Manor 
 
 
 M3H 
 North York 
 Downsview North
 
 
 M3H 
 North York 
 Wilson Heights 
 
 
 M4H 
 East York 
 Thorncliffe Park 
 
 
 M5H 
 Downtown Toronto 
 Adelaide
 
 
 M5H 
 Downtown Toronto 
 King
 
 
 M5H 
 Downtown Toronto 
 Richmond
 
 
 M6H 
 West Toronto 
 Dovercourt Village 
 
 
 M6H 
 West Toronto 
 Dufferin
 
 
 M7H 
 Not assigned 
 Not assigned
 
 
 M8H 
 Not assigned 
 Not assigned
 
 
 M9H 
 Not assigned 
 Not assigned
 
 
 M1J 
 Scarborough 
 Scarborough Village 
 
 
 M2J 
 North York 
 Fairview
 
 
 M2J 
 North York 
 Henry Farm 
 
 
 M2J 
 North York 
 Oriole
 
 
 M3J 
 North York 
 Northwood Park 
 
 
 M3J 
 North York 
 York University 
 
 
 M4J 
 East York 
 East Toronto 
 
 
 M5J 
 Downtown Toronto 
 Harbourfront East
 
 
 M5J 
 Downtown Toronto 
 Toronto Islands 
 
 
 M5J 
 Downtown Toronto 
 Union Station 
 
 
 M6J 
 West Toronto 
 Little Portugal 
 
 
 M6J 
 West Toronto 
 Trinity 
 
 
 M7J 
 Not assigned 
 Not assigned
 
 
 M8J 
 Not assigned 
 Not assigned
 
 
 M9J 
 Not assigned 
 Not assigned
 
 
 M1K 
 Scarborough 
 East Birchmount Park
 
 
 M1K 
 Scarborough 
 Ionview 
 
 
 M1K 
 Scarborough 
 Kennedy Park 
 
 
 M2K 
 North York 
 Bayview Village 
 
 
 M3K 
 North York 
 CFB Toronto 
 
 
 M3K 
 North York 
 Downsview East
 
 
 M4K 
 East Toronto 
 The Danforth West
 
 
 M4K 
 East Toronto 
 Riverdale 
 
 
 M5K 
 Downtown Toronto 
 Design Exchange 
 
 
 M5K 
 Downtown Toronto 
 Toronto Dominion Centre 
 
 
 M6K 
 West Toronto 


## Cleaning the DataFrame

In [61]:
dfs = pd.read_html(table)
df2=dfs[0]
df2.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

### Add Geo-spatial data

In [63]:
dfll= pd.read_csv("http://cocl.us/Geospatial_data")
dfll.rename(columns={'Postal Code':'Postcode'}, inplace=True)
dfll.set_index("Postcode")
df2.set_index("Postcode")
toronto_data=pd.merge(df2, dfll)
toronto_data.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M6A        North York  Lawrence Heights  43.718518 -79.464763
4      M6A        North York    Lawrence Manor  43.718518 -79.464763

## Use geopy library to get the latitude and longitude values of Toronto.

In order to define an instance of the geocoder, a user_agent is defined. The agent is named to_explorer, as shown below.

In [64]:
address = 'Toronto, ON, Canada'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto, ON, Canada are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto, ON, Canada are 43.653963, -79.387207.


### Create a map of Toronto with neighborhoods superimposed on top.

In [68]:
# create map of New York using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_data['Latitude'], toronto_data['Longitude'], toronto_data['Borough'], toronto_data['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Define Foursquare Credentials and Version

In [28]:
CLIENT_ID = 'OR2A1F3IR522FBM4SN4F3S21WNFXZTFIUHT2LEA1YJYFMV55' # your Foursquare ID
CLIENT_SECRET = 'YCKMUFHEX4CQCURKEPBS4OJ5LKBRENO3HQKX41YA4ZGEFRE3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OR2A1F3IR522FBM4SN4F3S21WNFXZTFIUHT2LEA1YJYFMV55
CLIENT_SECRET:YCKMUFHEX4CQCURKEPBS4OJ5LKBRENO3HQKX41YA4ZGEFRE3


 #### Let's explore the first neighborhood in our dataframe.

In [69]:
toronto_data.loc[0,'Neighbourhood']

'Parkwoods'

Get the neighborhood latitude and longitude 

In [70]:
neighborhood_latitude = toronto_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = toronto_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = toronto_data.loc[0, 'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


#### Now, let's get the top 100 venues that are in Parkwoods within a radius of 500 meters.
First, let's create the GET request URL. Name your URL url.

In [71]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=OR2A1F3IR522FBM4SN4F3S21WNFXZTFIUHT2LEA1YJYFMV55&client_secret=YCKMUFHEX4CQCURKEPBS4OJ5LKBRENO3HQKX41YA4ZGEFRE3&v=20180605&ll=43.7532586,-79.3296565&radius=500&limit=100'

Send the GET request and examine the resutls

In [72]:
results = requests.get(url).json()
#results

In [33]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a pandas dataframe.

In [34]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name         categories        lat        lng
0  Brookbanks Park               Park  43.751976 -79.332140
1    Variety Store  Food & Drink Shop  43.751974 -79.333114

In [35]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

2 venues were returned by Foursquare.


## 2. Explor Neighborhoods in Toronto, using k-Means Clustering:
Let's create a function to repeat the same process to all the neighborhoods in Toronto

In [77]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *Torronto_venues*.

In [78]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighbourhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront
Lawrence Heights
Lawrence Manor
Queen's Park
Islington Avenue
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design Exchange
Toro

#### Let's check the size of the resulting dataframe

In [79]:
print(toronto_venues.shape)
toronto_venues.head()

(4353, 7)


Neighbourhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

#### Let's check how many venues were returned for each neighborhood

In [80]:
toronto_venues.groupby('Neighbourhood').count()

Neighborhood Latitude  \
Neighbourhood                                                              
Adelaide                                                             100   
Agincourt                                                              5   
Agincourt North                                                        4   
Albion Gardens                                                        10   
Alderwood                                                              9   
Bathurst Manor                                                        19   
Bathurst Quay                                                         14   
Bayview Village                                                        4   
Beaumond Heights                                                      10   
Bedford Park                                                          25   
Berczy Park                                                           55   
Birch Cliff                                                            4   
Bloordale Gardens                                                      9   
Brockton                                                              22   
Business Reply Mail Processing Centre 969 Eastern                     15   
CFB Toronto                                                            2   
CN Tower                                                              14   
Cabbagetown                                                           43   
Caledonia-Fairbanks                                                    4   
Canada Post Gateway Processing Centre                                 13   
Cedarbrae                                                              8   
Central Bay Street                                                    82   
Chinatown                                                             89   
Christie                                                              17   
Church and Wellesley                                                  88   
Clairlea                                                              10   
Clarks Corners                                                        14   
Cliffcrest                                                             4   
Cliffside                                                              4   
Cliffside West                                                         4   
Cloverdale                                                             1   
Commerce Court                                                       100   
Davisville                                                            35   
Davisville North                                                       8   
Deer Park                                                             16   
Del Ray                                                                4   
Design Exchange                                                      100   
Don Mills North                                                        5   
Don Mills South                                                       23   
Dorset Park                                                            5   
Dovercourt Village                                                    19   
Downsview                                                              3   
Downsview Central                                                      4   
Downsview East                                                         2   
Downsview North                                                       19   
Downsview Northwest                                                    4   
Downsview West                                                         6   
Dufferin                                                              19   
East Birchmount Park                                                   6   
East Toronto                                                           4   
Emery                                                                  2   
Eringate               

#### Let's find out how many unique categories can be curated from all the returned venues

In [81]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 273 uniques categories.


### 3. Analyze Each Neighborhood

In [82]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighbourhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2  Victoria Village                  0                  0        0   
3  Victoria Village                  0                  0        0   
4  Victoria Village                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0     0    0               0                 0                   0      0   
1     0    0               0                 0                   0      0   
2     0    0               0                 0                   0      0   
3     0    0               0                 0                   0      0   
4     0    0               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0       

In [83]:
toronto_onehot.shape

(4353, 274)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [84]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                                             Adelaide           0.000000   
1                                            Agincourt           0.000000   
2                                      Agincourt North           0.000000   
3                                       Albion Gardens           0.000000   
4                                            Alderwood           0.000000   
5                                       Bathurst Manor           0.000000   
6                                        Bathurst Quay           0.000000   
7                                      Bayview Village           0.000000   
8                                     Beaumond Heights           0.000000   
9                                         Bedford Park           0.000000   
10                                         Berczy Park           0.000000   
11                                         Birch Cliff           0.000000   
12                                   Bloordale Gardens           0.000000   
13                                            Brockton           0.000000   
14   Business Reply Mail Processing Centre 969 Eastern           0.000000   
15                                         CFB Toronto           0.000000   
16                                            CN Tower           0.000000   
17                                         Cabbagetown           0.000000   
18                                 Caledonia-Fairbanks           0.000000   
19               Canada Post Gateway Processing Centre           0.000000   
20                                           Cedarbrae           0.000000   
21                                  Central Bay Street           0.000000   
22                                           Chinatown           0.000000   
23                                            Christie           0.000000   
24                                Church and Wellesley           0.000000   
25                                            Clairlea           0.000000   
26                                      Clarks Corners           0.000000   
27                                          Cliffcrest           0.000000   
28                                           Cliffside           0.000000   
29                                      Cliffside West           0.000000   
30                                          Cloverdale           0.000000   
31                                      Commerce Court           0.000000   
32                                          Davisville           0.000000   
33                                    Davisville North           0.000000   
34                                           Deer Park           0.000000   
35                                             Del Ray           0.000000   
36                                     Design Exchange           0.000000   
37                                     Don Mills North           0.000000   
38                                     Don Mills South           0.000000   
39                                         Dorset Park           0.000000   
40                                  Dovercourt Village           0.000000   
41                                           Downsview           0.000000   
42                                   Downsview Central           0.000000   
43                                      Downsview East           0.000000   
44                                     Downsview North           0.000000   
45                                 Downsview Northwest           0.000000   
46                                      Downsview West           0.000000   
47                                            Dufferin           0.000000   
48                                East Birchmount Park           0.000000   
49                                        East Toronto           0.000000   
50                                               Emery           0.000000   
51                                   

In [85]:
toronto_grouped.shape

(204, 274)

#### Let's print each neighborhood along with the top 5 most common venues

In [86]:
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
             venue  freq
0      Coffee Shop  0.07
1       Restaurant  0.05
2             Café  0.04
3  Thai Restaurant  0.04
4              Bar  0.03


----Agincourt----
                       venue  freq
0                     Lounge   0.2
1  Latin American Restaurant   0.2
2             Breakfast Spot   0.2
3             Clothing Store   0.2
4               Skating Rink   0.2


----Agincourt North----
                      venue  freq
0                      Park  0.25
1                    Bakery  0.25
2                Playground  0.25
3               Coffee Shop  0.25
4  Mediterranean Restaurant  0.00


----Albion Gardens----
                  venue  freq
0         Grocery Store   0.2
1  Fast Food Restaurant   0.1
2           Pizza Place   0.1
3   Fried Chicken Joint   0.1
4   Japanese Restaurant   0.1


----Alderwood----
          venue  freq
0   Pizza Place  0.22
1           Gym  0.11
2  Skating Rink  0.11
3           Pub  0.11
4      Pharmacy  0.11


----Bathurst M

           venue  freq
0  Grocery Store  0.33
1           Park  0.17
2           Bank  0.17
3  Shopping Mall  0.17
4          Hotel  0.17


----Dufferin----
                  venue  freq
0              Pharmacy  0.11
1                Bakery  0.11
2           Pizza Place  0.11
3                  Pool  0.05
4  Fast Food Restaurant  0.05


----East Birchmount Park----
               venue  freq
0     Discount Store  0.33
1   Department Store  0.17
2  Convenience Store  0.17
3         Hobby Shop  0.17
4        Coffee Shop  0.17


----East Toronto----
                       venue  freq
0                       Park  0.50
1              Metro Station  0.25
2          Convenience Store  0.25
3             Massage Studio  0.00
4  Middle Eastern Restaurant  0.00


----Emery----
                       venue  freq
0     Furniture / Home Store   0.5
1             Baseball Field   0.5
2   Mediterranean Restaurant   0.0
3         Miscellaneous Shop   0.0
4  Middle Eastern Restaurant   0.0


----Ering

                       venue  freq
0                       Park  0.33
1                Pizza Place  0.33
2             Sandwich Place  0.33
3             Medical Center  0.00
4  Middle Eastern Restaurant  0.00


----Kingsway Park South East----
                       venue  freq
0                  Locksmith   0.5
1             Baseball Field   0.5
2          Accessories Store   0.0
3             Medical Center   0.0
4  Middle Eastern Restaurant   0.0


----Kingsway Park South West----
            venue  freq
0             Gym  0.08
1          Bakery  0.08
2  Hardware Store  0.08
3  Discount Store  0.08
4  Sandwich Place  0.08


----L'Amoreaux East----
                      venue  freq
0                      Park  0.25
1                    Bakery  0.25
2                Playground  0.25
3               Coffee Shop  0.25
4  Mediterranean Restaurant  0.00


----L'Amoreaux West----
                  venue  freq
0  Fast Food Restaurant  0.17
1    Chinese Restaurant  0.17
2              Pharm

                       venue  freq
0                  Gift Shop   1.0
1          Accessories Store   0.0
2             Massage Studio   0.0
3  Middle Eastern Restaurant   0.0
4         Mexican Restaurant   0.0


----Queen's Park----
                 venue  freq
0          Coffee Shop  0.21
1                 Park  0.05
2                  Gym  0.02
3  Fried Chicken Joint  0.02
4         Burger Joint  0.02


----Railway Lands----
             venue  freq
0   Airport Lounge  0.14
1  Airport Service  0.14
2         Boutique  0.07
3      Coffee Shop  0.07
4          Airport  0.07


----Rathnelly----
          venue  freq
0           Pub  0.12
1   Coffee Shop  0.12
2  Liquor Store  0.06
3   Pizza Place  0.06
4          Bank  0.06


----Richmond----
             venue  freq
0      Coffee Shop  0.07
1       Restaurant  0.05
2             Café  0.04
3  Thai Restaurant  0.04
4              Bar  0.03


----Richview Gardens----
                       venue  freq
0                       Park  0.33
1

                 venue  freq
0      Thai Restaurant  0.09
1   Mexican Restaurant  0.09
2                 Café  0.09
3                  Bar  0.09
4  Arts & Crafts Store  0.04


----The Kingsway----
          venue  freq
0          Park   0.5
1         River   0.5
2  Optical Shop   0.0
3   Opera House   0.0
4  Liquor Store   0.0


----The Queensway East----
                       venue  freq
0                  Locksmith   0.5
1             Baseball Field   0.5
2          Accessories Store   0.0
3             Medical Center   0.0
4  Middle Eastern Restaurant   0.0


----The Queensway West----
            venue  freq
0             Gym  0.08
1          Bakery  0.08
2  Hardware Store  0.08
3  Discount Store  0.08
4  Sandwich Place  0.08


----Thistletown----
                  venue  freq
0         Grocery Store   0.2
1  Fast Food Restaurant   0.1
2           Pizza Place   0.1
3   Fried Chicken Joint   0.1
4   Japanese Restaurant   0.1


----Thorncliffe Park----
               venue  freq
0  

#### Let's put that into a pandas dataframe
First, let's write a function to sort the venues in descending order.

In [87]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

#### Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [88]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighbourhood      1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide                Coffee Shop            Restaurant   
1        Agincourt  Latin American Restaurant        Breakfast Spot   
2  Agincourt North                       Park                Bakery   
3   Albion Gardens              Grocery Store            Beer Store   
4        Alderwood                Pizza Place                   Gym   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0       Thai Restaurant                  Café            Steakhouse   
1        Clothing Store                Lounge          Skating Rink   
2           Coffee Shop            Playground           Yoga Studio   
3        Sandwich Place   Fried Chicken Joint  Fast Food Restaurant   
4              Pharmacy        Sandwich Place          Skating Rink   

  6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
0                   Bar                          Gym                Bakery   
1     Electronics Store  Eastern European Restaurant   Empanada Restaurant   
2               Dog Run                 Dessert Shop    Dim Sum Restaurant   
3        Discount Store                     Pharmacy           Pizza Place   
4                  Pool                          Pub           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
0    Seafood Restaurant            Pizza Place  
1   Dumpling Restaurant           Dessert Shop  
2                 Diner         Discount Store  
3   Japanese Restaurant     Dim Sum Restaurant  
4            Comic Shop           Dance Studio

### 4. Cluster Neighborhoods
Run k-means to cluster the neighborhood into 5 clusters.

In [89]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 2, 0, 0, 0, 0, 0, 0, 0])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [90]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')



# check the last columns!
toronto_merged.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude  \
0      M3A        North York         Parkwoods  43.753259 -79.329656   
1      M4A        North York  Victoria Village  43.725882 -79.315572   
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3      M6A        North York  Lawrence Heights  43.718518 -79.464763   
4      M6A        North York    Lawrence Manor  43.718518 -79.464763   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             2.0                  Park     Food & Drink Shop   
1             0.0          Hockey Arena           Coffee Shop   
2             0.0           Coffee Shop                Bakery   
3             0.0        Clothing Store     Accessories Store   
4             0.0        Clothing Store     Accessories Store   

        3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0                 Yoga Studio                Dog Run          Dessert Shop   
1  Financial or Legal Service  Portuguese Restaurant           Yoga Studio   
2                         Pub                   Park               Theater   
3      Furniture / Home Store            Coffee Shop    Miscellaneous Shop   
4      Furniture / Home Store            Coffee Shop    Miscellaneous Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    Dim Sum Restaurant                 Diner        Discount Store   
1          Dessert Shop    Dim Sum Restaurant                 Diner   
2            Restaurant                  Café    Mexican Restaurant   
3            Shoe Store              Boutique           Event Space   
4            Shoe Store              Boutique           Event Space   

   9th Most Common Venue 10th Most Common Venue  
0    Distribution Center       Doner Restaurant  
1         Discount Store    Distribution Center  
2            Event Space         Chocolate Shop  
3  Vietnamese Restaurant              Gift Shop  
4  Vietnamese Restaurant              Gift Shop

In [91]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        #color=rainbow[cluster-1],
        fill=True,
        #fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### 5. Examine Clusters
Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1

In [98]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels      1st Most Common Venue  \
1          North York             0.0               Hockey Arena   
2    Downtown Toronto             0.0                Coffee Shop   
3          North York             0.0             Clothing Store   
4          North York             0.0             Clothing Store   
5    Downtown Toronto             0.0                Coffee Shop   
9          North York             0.0        Japanese Restaurant   
10          East York             0.0                Pizza Place   
11          East York             0.0                Pizza Place   
12   Downtown Toronto             0.0                Coffee Shop   
13   Downtown Toronto             0.0                Coffee Shop   
23         North York             0.0                        Gym   
24         North York             0.0                        Gym   
25          East York             0.0               Skating Rink   
26   Downtown Toronto             0.0                Coffee Shop   
27               York             0.0                      Field   
28          Etobicoke             0.0          Convenience Store   
29          Etobicoke             0.0          Convenience Store   
30          Etobicoke             0.0          Convenience Store   
31          Etobicoke             0.0          Convenience Store   
32        Scarborough             0.0          Electronics Store   
33        Scarborough             0.0          Electronics Store   
34        Scarborough             0.0          Electronics Store   
35       East Toronto             0.0                      Trail   
36   Downtown Toronto             0.0                Coffee Shop   
38        Scarborough             0.0                Coffee Shop   
39          East York             0.0     Furniture / Home Store   
40   Downtown Toronto             0.0                Coffee Shop   
41   Downtown Toronto             0.0              Grocery Store   
42        Scarborough             0.0                Gas Station   
43         North York             0.0                    Dog Run   
44         North York             0.0                       Bank   
45         North York             0.0                       Bank   
46         North York             0.0                       Bank   
47          East York             0.0          Indian Restaurant   
48   Downtown Toronto             0.0                Coffee Shop   
49   Downtown Toronto             0.0                Coffee Shop   
50   Downtown Toronto             0.0                Coffee Shop   
51       West Toronto             0.0                     Bakery   
52       West Toronto             0.0                     Bakery   
54         North York             0.0             Clothing Store   
55         North York             0.0             Clothing Store   
56         North York             0.0             Clothing Store   
57         North York             0.0             Massage Studio   
58         North York             0.0             Massage Studio   
60   Downtown Toronto             0.0                Coffee Shop   
61   Downtown Toronto             0.0                Coffee Shop   
62   Downtown Toronto             0.0                Coffee Shop   
63       West Toronto             0.0                        Bar   
64       West Toronto             0.0                        Bar   
65        Scarborough             0.0             Discount Store   
66        Scarborough             0.0             Discount Store   
67        Scarborough             0.0             Discount Store   
68         North York             0.0                       Café   
71       East Toronto             0.0           Greek Restaurant   
72       East Toronto             0.0           Greek Restaurant   
73   Downtown Toronto             0.0                Coffee Shop   
74   Downtown Toronto             0.0                Coffee Shop   
75       West Toronto             0.0             Breakfast Spot   
76

#### Cluster 2

In [99]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
7  Scarborough             1.0  Fast Food Restaurant           Yoga Studio   
8  Scarborough             1.0  Fast Food Restaurant           Yoga Studio   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
7      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   
8      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
7                 Diner        Discount Store   Distribution Center   
8                 Diner        Discount Store   Distribution Center   

  9th Most Common Venue 10th Most Common Venue  
7               Dog Run             Donut Shop  
8               Dog Run             Donut Shop

#### Cluster 3

In [101]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0          North York             2.0                  Park   
14         North York             2.0                  Park   
20        Scarborough             2.0                   Bar   
21        Scarborough             2.0                   Bar   
22        Scarborough             2.0                   Bar   
37               York             2.0                  Park   
53        Scarborough             2.0            Playground   
59          East York             2.0                  Park   
69         North York             2.0                  Park   
70         North York             2.0                  Park   
81         North York             2.0             Cafeteria   
82         North York             2.0             Cafeteria   
88         North York             2.0                  Park   
89         North York             2.0                  Park   
90         North York             2.0                  Park   
111   Central Toronto             2.0  Gym / Fitness Center   
119        North York             2.0                  Park   
121   Central Toronto             2.0                  Park   
122   Central Toronto             2.0                  Park   
136         Etobicoke             2.0                  Park   
137         Etobicoke             2.0                  Park   
138         Etobicoke             2.0                  Park   
139         Etobicoke             2.0                  Park   
149   Central Toronto             2.0                   Gym   
150   Central Toronto             2.0                   Gym   
154       Scarborough             2.0                  Park   
155       Scarborough             2.0                  Park   
156       Scarborough             2.0                  Park   
157       Scarborough             2.0                  Park   
182  Downtown Toronto             2.0                  Park   
192         Etobicoke             2.0                 River   
193         Etobicoke             2.0                 River   
194         Etobicoke             2.0                 River   

          2nd Most Common Venue       3rd Most Common Venue  \
0             Food & Drink Shop                 Yoga Studio   
14                          Pub            Sushi Restaurant   
20                  Yoga Studio            Doner Restaurant   
21                  Yoga Studio            Doner Restaurant   
22                  Yoga Studio            Doner Restaurant   
37                Women's Store                      Market   
53   Construction & Landscaping                 Yoga Studio   
59            Convenience Store               Metro Station   
69                      Airport                 Yoga Studio   
70                      Airport                 Yoga Studio   
81             Doner Restaurant                Dessert Shop   
82             Doner Restaurant                Dessert Shop   
88                       Bakery  Construction & Landscaping   
89                       Bakery  Construction & Landscaping   
90                       Bakery  Construction & Landscaping   
111                        Park                 Swim School   
119                        Bank           Convenience Store   
121               Jewelry Store            Sushi Restaurant   
122               Jewelry Store            Sushi Restaurant   
136                 Pizza Place              Sandwich Place   
137                 Pizza Place              Sandwich Place   
138                 Pizza Place              Sandwich Place   
139                 Pizza Place              Sandwich Place   
149                        Park                Tennis Court   
150                        Park                Tennis Court   
154                      Bakery                 Coffee Shop   
155                      Bakery                 Coffee Shop   
156                      Bakery                 Coffee Shop   
157                      Bakery             

#### Cluster 4

In [102]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
15  Etobicoke             3.0             Gift Shop           Yoga Studio   
16  Etobicoke             3.0             Gift Shop           Yoga Studio   
17  Etobicoke             3.0             Gift Shop           Yoga Studio   
18  Etobicoke             3.0             Gift Shop           Yoga Studio   
19  Etobicoke             3.0             Gift Shop           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
15      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   
16      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   
17      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   
18      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   
19      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
15                 Diner        Discount Store   Distribution Center   
16                 Diner        Discount Store   Distribution Center   
17                 Diner        Discount Store   Distribution Center   
18                 Diner        Discount Store   Distribution Center   
19                 Diner        Discount Store   Distribution Center   

   9th Most Common Venue 10th Most Common Venue  
15               Dog Run             Donut Shop  
16               Dog Run             Donut Shop  
17               Dog Run             Donut Shop  
18               Dog Run             Donut Shop  
19               Dog Run             Donut Shop

#### Cluster 5 

In [103]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels   1st Most Common Venue 2nd Most Common Venue  \
105  North York             4.0  Furniture / Home Store        Baseball Field   
106  North York             4.0  Furniture / Home Store        Baseball Field   
197   Etobicoke             4.0               Locksmith        Baseball Field   
198   Etobicoke             4.0               Locksmith        Baseball Field   
199   Etobicoke             4.0               Locksmith        Baseball Field   
200   Etobicoke             4.0               Locksmith        Baseball Field   
201   Etobicoke             4.0               Locksmith        Baseball Field   
202   Etobicoke             4.0               Locksmith        Baseball Field   
203   Etobicoke             4.0               Locksmith        Baseball Field   
204   Etobicoke             4.0               Locksmith        Baseball Field   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
105           Yoga Studio      Department Store    Dim Sum Restaurant   
106           Yoga Studio      Department Store    Dim Sum Restaurant   
197           Yoga Studio            Donut Shop                 Diner   
198           Yoga Studio            Donut Shop                 Diner   
199           Yoga Studio            Donut Shop                 Diner   
200           Yoga Studio            Donut Shop                 Diner   
201           Yoga Studio            Donut Shop                 Diner   
202           Yoga Studio            Donut Shop                 Diner   
203           Yoga Studio            Donut Shop                 Diner   
204           Yoga Studio            Donut Shop                 Diner   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
105                 Diner        Discount Store   Distribution Center   
106                 Diner        Discount Store   Distribution Center   
197        Discount Store   Distribution Center               Dog Run   
198        Discount Store   Distribution Center               Dog Run   
199        Discount Store   Distribution Center               Dog Run   
200        Discount Store   Distribution Center               Dog Run   
201        Discount Store   Distribution Center               Dog Run   
202        Discount Store   Distribution Center               Dog Run   
203        Discount Store   Distribution Center               Dog Run   
204        Discount Store   Distribution Center               Dog Run   

    9th Most Common Venue 10th Most Common Venue  
105               Dog Run       Doner Restaurant  
106               Dog Run       Doner Restaurant  
197      Doner Restaurant              Drugstore  
198      Doner Restaurant              Drugstore  
199      Doner Restaurant              Drugstore  
200      Doner Restaurant              Drugstore  
201      Doner Restaurant              Drugstore  
202      Doner Restaurant              Drugstore  
203      Doner Restaurant              Drugstore  
204      Doner Restaurant              Drugstore